In [1]:
#IMPORTING LIBRARIES
    
from nptdms import TdmsFile
import numpy as np
import pandas as pd
import matplotlib as plt
import matplotlib.pyplot as plt
import scipy as sp
from scipy import signal
from scipy.signal import chirp, find_peaks, peak_widths
from scipy import io
from scipy import sparse
from scipy.linalg import solveh_banded
from scipy.sparse.linalg import spsolve
from statistics import mean
#import mpld3
#mpld3.enable_notebook()
%matplotlib inline
plt.rcParams['agg.path.chunksize'] = 1000000

###############################################################################################\n",
###############################################################################################\n",
###############################################################################################\n",
###############################################################################################\n",

#LOADING THE TDMS FILE

num_to_plot = 5
    
for i in range(0,num_to_plot):

    tdms_file = TdmsFile("G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_%s.tdms"%i)
    tdms_groups = tdms_file.groups()
    attributes = tdms_file.object().properties 
    tdms_0 = tdms_file.group_channels("Untitled")
    tdms_1 = tdms_file.group_channels("Untitled")
    Group_Channel_0_1 = tdms_file.object('Untitled', 'Current (nA)')
    Group_Channel_data_0_1 = Group_Channel_0_1.data
    Group_Channel_1_1 = tdms_file.object('Untitled', 'Time (s)')
    Group_Channel_data_1_1 = Group_Channel_1_1.data
    Group_Channel_Current = (Group_Channel_data_0_1)
    print("shape of GCC", Group_Channel_Current.shape)
    X= Group_Channel_data_1_1
    Y= Group_Channel_Current
    #x = np.linspace(0,Group_Channel_Current.shape[0],Group_Channel_Current.shape[0]  )*(1/50000)
    plt.plot(X,Y)
    plt.savefig("Raw_Signal_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).png"%i, bbox_inches="tight", dpi=600)
    #plt.show()
    #narr_curr = np.column_stack((x, Group_Channel_Current))
    #io.savemat("Raw_Signal_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).mat"%i, {"array": narr_curr})
    plt.close()  
    z= Y.shape[0]
    def moving_average(x,w):
        return np.convolve(x,np.ones(w),'valid')/w
    window=int(round((z/50000)*1000))
    mov_curr= moving_average(Y,window)
    #avg_mov_curr= mean(mov_curr)
    #print(avg_mov_curr)
    print(len(mov_curr))
    a=len(mov_curr)
    print('moving average current', mov_curr) 
    b=mov_curr[-1]
    print(b)
    mov_curr= np.ndarray.tolist(mov_curr)
    mov_curr+=(window-1)*[b]
    print('length', z)
    print('moving current extended',len(mov_curr))
    temp=[]
    ## zero is open polymerase, looking for dntp ## 
    ## one is closed polymerase, matching the found dntp with the complementary base in the template ##
    for j in range (z):
        if Y[j]>=mov_curr[j]:
            temp.append(1)
        else:
            temp.append(0)
    print(len(temp))
    #Y_new=np.asarray(temp)*(-1)
    print(Y.shape)
    plt.plot(X,temp)
    #plt.show()
    plt.savefig("State_closed_&_open_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).png"%i, bbox_inches="tight", dpi=600)
    plt.close()
    
    #############################################
    
    temp_1 = []
    temp_0 = []
    
    count_1 = 0
    count_0 = 0
    for k in range(0,len(temp)):
        if temp[k] == 1:
            if (k<len(temp)-1):
                if(temp[k+1]!=0):
                    count_1 += 1
                elif(temp[k] == 1 and temp[k+1]==0):
                    print('count 1',count_1)
                    temp_1.append(count_1)
                    count_1 = 0
            elif(k==len(temp)):
                temp_1.append(1)
        else:
            if(k<len(temp)-1):
                if(temp[k+1]!=1):
                    count_0 +=1
                elif(temp[k] == 0 and temp[k+1]==1):
                    print('count 0',count_0)
                    temp_0.append(count_0)
                    count_0 = 0
            elif(k==len(temp)):
                temp_0.append(0)        
                
        #print(count_1) 
   
    print("temp1", (temp_1))
    print("temp0", (temp_0)) 
    plt.yticks(size=14);
    plt.xticks(size=14);
    plt.ylabel('Count', size=14)
    plt.xlabel('Duration_of_state_closed', size=14)
    plt.xlim(xmin=-10, xmax = 300)
    plt.hist(temp_1, bins='auto',edgecolor='black',facecolor='green')
    plt.savefig("Duration_of_state_closed_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).png"%i, bbox_inches="tight", dpi=600)
    #plt.show()
    io.savemat("Duration_of_state_closed_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).mat"%i, {"array": temp_1}, oned_as='column')
    plt.close()
    plt.yticks(size=14);
    plt.xticks(size=14);
    plt.ylabel('Count', size=14)
    plt.xlabel('Duration_of_state_open', size=14)
    plt.xlim(xmin=-10, xmax = 300)
    plt.hist(temp_0, bins='auto',edgecolor='black',facecolor='blue')
    plt.savefig("Duration_of_state_open_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).png"%i, bbox_inches="tight", dpi=600)
    #plt.show()
    io.savemat("Duration_of_state_open_G3G4_SHBiotin_SA_phi29_Temp_dNTP_Mg_50mV_(%s).mat"%i, {"array": temp_0}, oned_as='column')
    plt.close()
    

shape of GCC (1505220,)
1475117
moving average current [1.23853668 1.23853654 1.23853664 ... 1.22834821 1.22834923 1.22835003]
1.2283500255992426
length 1505220
moving current extended 1505220
1505220
(1505220,)
count 0 59
count 1 41
count 0 109
count 1 53
count 0 7
count 1 0
count 0 1
count 1 1
count 0 3
count 1 85
count 0 26
count 1 9
count 0 169
count 1 57
count 0 90
count 1 4
count 0 15
count 1 3
count 0 15
count 1 120
count 0 30
count 1 17
count 0 56
count 1 18
count 0 21
count 1 11
count 0 43
count 1 64
count 0 37
count 1 1
count 0 1
count 1 0
count 0 11
count 1 17
count 0 11
count 1 3
count 0 20
count 1 8
count 0 12
count 1 135
count 0 84
count 1 145
count 0 127
count 1 27
count 0 202
count 1 31
count 0 2
count 1 91
count 0 114
count 1 6
count 0 51
count 1 33
count 0 41
count 1 76
count 0 25
count 1 2
count 0 26
count 1 31
count 0 54
count 1 12
count 0 61
count 1 1
count 0 87
count 1 45
count 0 15
count 1 3
count 0 69
count 1 145
count 0 20
count 1 0
count 0 9
count 1 3
count 0 

count 1 63
count 0 28
count 1 10
count 0 106
count 1 50
count 0 78
count 1 23
count 0 37
count 1 17
count 0 39
count 1 10
count 0 68
count 1 37
count 0 6
count 1 18
count 0 106
count 1 25
count 0 67
count 1 23
count 0 8
count 1 54
count 0 140
count 1 24
count 0 82
count 1 68
count 0 105
count 1 13
count 0 68
count 1 20
count 0 73
count 1 164
count 0 20
count 1 51
count 0 16
count 1 6
count 0 13
count 1 20
count 0 52
count 1 3
count 0 33
count 1 3
count 0 15
count 1 65
count 0 4
count 1 15
count 0 6
count 1 32
count 0 8
count 1 7
count 0 7
count 1 9
count 0 20
count 1 20
count 0 37
count 1 9
count 0 51
count 1 21
count 0 40
count 1 24
count 0 5
count 1 9
count 0 38
count 1 23
count 0 116
count 1 36
count 0 27
count 1 5
count 0 38
count 1 92
count 0 16
count 1 71
count 0 9
count 1 80
count 0 17
count 1 13
count 0 19
count 1 134
count 0 4
count 1 17
count 0 49
count 1 12
count 0 12
count 1 11
count 0 30
count 1 30
count 0 13
count 1 40
count 0 2
count 1 1
count 0 25
count 1 16
count 0 60


count 0 3
count 1 22
count 0 0
count 1 29
count 0 3
count 1 15
count 0 7
count 1 40
count 0 0
count 1 2
count 0 2
count 1 0
count 0 3
count 1 0
count 0 2
count 1 10
count 0 9
count 1 21
count 0 0
count 1 13
count 0 1
count 1 0
count 0 0
count 1 15
count 0 3
count 1 15
count 0 11
count 1 189
count 0 5
count 1 110
count 0 5
count 1 20
count 0 3
count 1 49
count 0 4
count 1 10
count 0 8
count 1 28
count 0 10
count 1 21
count 0 4
count 1 4
count 0 19
count 1 20
count 0 0
count 1 18
count 0 0
count 1 29
count 0 6
count 1 25
count 0 10
count 1 30
count 0 6
count 1 2
count 0 0
count 1 8
count 0 52
count 1 7
count 0 12
count 1 10
count 0 11
count 1 5
count 0 1
count 1 1
count 0 2
count 1 19
count 0 1
count 1 18
count 0 15
count 1 96
count 0 9
count 1 14
count 0 0
count 1 96
count 0 3
count 1 21
count 0 22
count 1 29
count 0 25
count 1 12
count 0 39
count 1 8
count 0 22
count 1 34
count 0 11
count 1 0
count 0 31
count 1 10
count 0 22
count 1 0
count 0 1
count 1 13
count 0 48
count 1 12
count 0 

count 1 73
count 0 17
count 1 2
count 0 2
count 1 193
count 0 15
count 1 14
count 0 1
count 1 19
count 0 14
count 1 14
count 0 7
count 1 99
count 0 71
count 1 39
count 0 7
count 1 83
count 0 77
count 1 21
count 0 21
count 1 12
count 0 9
count 1 10
count 0 9
count 1 10
count 0 102
count 1 48
count 0 104
count 1 22
count 0 29
count 1 15
count 0 14
count 1 4
count 0 23
count 1 35
count 0 51
count 1 27
count 0 54
count 1 18
count 0 5
count 1 109
count 0 20
count 1 75
count 0 13
count 1 12
count 0 39
count 1 87
count 0 47
count 1 19
count 0 100
count 1 20
count 0 23
count 1 2
count 0 25
count 1 4
count 0 15
count 1 0
count 0 106
count 1 18
count 0 18
count 1 117
count 0 47
count 1 102
count 0 39
count 1 14
count 0 26
count 1 24
count 0 56
count 1 11
count 0 135
count 1 114
count 0 177
count 1 11
count 0 289
count 1 64
count 0 207
count 1 41
count 0 74
count 1 82
count 0 71
count 1 50
count 0 12
count 1 37
count 0 23
count 1 82
count 0 17
count 1 7
count 0 83
count 1 67
count 0 115
count 1 6

count 1 94
count 0 20
count 1 33
count 0 68
count 1 85
count 0 19
count 1 132
count 0 96
count 1 18
count 0 39
count 1 42
count 0 5
count 1 18
count 0 1
count 1 6
count 0 154
count 1 34
count 0 45
count 1 36
count 0 66
count 1 18
count 0 3
count 1 63
count 0 204
count 1 10
count 0 124
count 1 43
count 0 281
count 1 12
count 0 14
count 1 43
count 0 149
count 1 12
count 0 151
count 1 50
count 0 550
count 1 116
count 0 29
count 1 51
count 0 11
count 1 10
count 0 53
count 1 76
count 0 61
count 1 23
count 0 23
count 1 109
count 0 35
count 1 205
count 0 13
count 1 53
count 0 42
count 1 70
count 0 173
count 1 150
count 0 16
count 1 5
count 0 126
count 1 37
count 0 92
count 1 103
count 0 82
count 1 57
count 0 85
count 1 10
count 0 40
count 1 7
count 0 15
count 1 10
count 0 304
count 1 136
count 0 28
count 1 24
count 0 101
count 1 10
count 0 192
count 1 90
count 0 43
count 1 26
count 0 127
count 1 61
count 0 127
count 1 11
count 0 175
count 1 178
count 0 51
count 1 12
count 0 49
count 1 20
coun

...

count 0 72
count 1 15
count 0 8
count 1 63
count 0 74
count 1 83
count 0 3
count 1 17
count 0 56
count 1 67
count 0 4
count 1 8
count 0 9
count 1 16
count 0 21
count 1 35
count 0 68
count 1 8
count 0 33
count 1 1
count 0 52
count 1 7
count 0 53
count 1 9
count 0 66
count 1 12
count 0 114
count 1 40
count 0 22
count 1 44
count 0 184
count 1 8
count 0 27
count 1 0
count 0 41
count 1 3
count 0 4
count 1 62
count 0 96
count 1 30
count 0 30
count 1 27
count 0 0
count 1 0
count 0 32
count 1 19
count 0 10
count 1 8
count 0 30
count 1 3
count 0 7
count 1 29
count 0 120
count 1 71
count 0 6
count 1 11
count 0 14
count 1 37
count 0 13
count 1 22
count 0 35
count 1 0
count 0 0
count 1 4
count 0 23
count 1 36
count 0 11
count 1 1
count 0 0
count 1 83
count 0 18
count 1 5
count 0 11
count 1 5
count 0 68
count 1 7
count 0 105
count 1 5
count 0 10
count 1 1
count 0 0
count 1 14
count 0 9
count 1 17
count 0 9
count 1 27
count 0 5
count 1 92
count 0 20
count 1 28
count 0 21
count 1 2
count 0 8
count 1 

count 0 115
count 1 29
count 0 26
count 1 4
count 0 15
count 1 15
count 0 23
count 1 12
count 0 104
count 1 30
count 0 2
count 1 34
count 0 8
count 1 18
count 0 100
count 1 12
count 0 64
count 1 25
count 0 7
count 1 16
count 0 1
count 1 0
count 0 7
count 1 6
count 0 4
count 1 9
count 0 5
count 1 17
count 0 5
count 1 21
count 0 66
count 1 7
count 0 14
count 1 11
count 0 100
count 1 68
count 0 12
count 1 1
count 0 18
count 1 9
count 0 18
count 1 9
count 0 21
count 1 7
count 0 22
count 1 6
count 0 0
count 1 1
count 0 7
count 1 46
count 0 3
count 1 32
count 0 16
count 1 1
count 0 19
count 1 0
count 0 16
count 1 2
count 0 0
count 1 24
count 0 23
count 1 15
count 0 40
count 1 85
count 0 15
count 1 57
count 0 35
count 1 131
count 0 9
count 1 53
count 0 3
count 1 0
count 0 6
count 1 3
count 0 18
count 1 24
count 0 8
count 1 13
count 0 2
count 1 82
count 0 12
count 1 92
count 0 7
count 1 65
count 0 0
count 1 32
count 0 103
count 1 14
count 0 70
count 1 1
count 0 0
count 1 0
count 0 44
count 1 8

count 1 44
count 0 47
count 1 20
count 0 60
count 1 10
count 0 15
count 1 10
count 0 39
count 1 2
count 0 12
count 1 5
count 0 19
count 1 98
count 0 33
count 1 7
count 0 5
count 1 44
count 0 30
count 1 31
count 0 48
count 1 65
count 0 6
count 1 0
count 0 43
count 1 19
count 0 17
count 1 21
count 0 3
count 1 16
count 0 2
count 1 4
count 0 9
count 1 6
count 0 64
count 1 20
count 0 29
count 1 18
count 0 45
count 1 27
count 0 27
count 1 4
count 0 16
count 1 11
count 0 26
count 1 4
count 0 7
count 1 10
count 0 5
count 1 7
count 0 18
count 1 12
count 0 9
count 1 10
count 0 29
count 1 185
count 0 16
count 1 34
count 0 22
count 1 11
count 0 10
count 1 5
count 0 20
count 1 11
count 0 10
count 1 6
count 0 6
count 1 64
count 0 8
count 1 20
count 0 50
count 1 25
count 0 4
count 1 28
count 0 9
count 1 10
count 0 8
count 1 34
count 0 23
count 1 3
count 0 11
count 1 13
count 0 0
count 1 2
count 0 10
count 1 5
count 0 9
count 1 12
count 0 14
count 1 14
count 0 30
count 1 4
count 0 5
count 1 36
count 0

count 1 5
count 0 38
count 1 39
count 0 26
count 1 5
count 0 72
count 1 18
count 0 7
count 1 11
count 0 34
count 1 4
count 0 20
count 1 10
count 0 5
count 1 3
count 0 7
count 1 9
count 0 11
count 1 1
count 0 49
count 1 50
count 0 13
count 1 8
count 0 28
count 1 10
count 0 1
count 1 12
count 0 30
count 1 4
count 0 26
count 1 46
count 0 17
count 1 1
count 0 13
count 1 22
count 0 9
count 1 11
count 0 21
count 1 7
count 0 33
count 1 68
count 0 45
count 1 8
count 0 52
count 1 40
count 0 2
count 1 4
count 0 50
count 1 21
count 0 9
count 1 33
count 0 45
count 1 42
count 0 32
count 1 25
count 0 17
count 1 48
count 0 51
count 1 13
count 0 8
count 1 11
count 0 0
count 1 0
count 0 9
count 1 25
count 0 15
count 1 23
count 0 13
count 1 28
count 0 9
count 1 16
count 0 56
count 1 24
count 0 19
count 1 15
count 0 24
count 1 15
count 0 12
count 1 4
count 0 23
count 1 20
count 0 8
count 1 7
count 0 27
count 1 12
count 0 0
count 1 0
count 0 16
count 1 6
count 0 15
count 1 17
count 0 10
count 1 1
count 0 

count 0 15
count 1 18
count 0 5
count 1 10
count 0 12
count 1 8
count 0 17
count 1 13
count 0 15
count 1 19
count 0 3
count 1 47
count 0 7
count 1 52
count 0 7
count 1 11
count 0 12
count 1 25
count 0 9
count 1 3
count 0 4
count 1 10
count 0 27
count 1 4
count 0 12
count 1 22
count 0 7
count 1 20
count 0 17
count 1 29
count 0 4
count 1 27
count 0 14
count 1 11
count 0 3
count 1 23
count 0 11
count 1 14
count 0 10
count 1 3
count 0 2
count 1 9
count 0 10
count 1 66
count 0 3
count 1 1
count 0 3
count 1 19
count 0 7
count 1 0
count 0 8
count 1 9
count 0 18
count 1 12
count 0 26
count 1 12
count 0 7
count 1 41
count 0 4
count 1 16
count 0 18
count 1 2
count 0 11
count 1 11
count 0 5
count 1 15
count 0 17
count 1 2
count 0 15
count 1 14
count 0 11
count 1 4
count 0 9
count 1 4
count 0 1
count 1 0
count 0 13
count 1 9
count 0 6
count 1 4
count 0 13
count 1 11
count 0 10
count 1 8
count 0 14
count 1 7
count 0 25
count 1 8
count 0 40
count 1 7
count 0 11
count 1 7
count 0 0
count 1 0
count 0 